<img id="top" style="float:left;height:100px;" src="http://ich.cnam.fr/medias/photo/omnes-ubique-docet_1472542836182-gif?ID_FICHE=580363">
<a style="float:right;" href="http://www.cnam.fr//"><img style="height:80px;" src="https://upload.wikimedia.org/wikipedia/commons/6/66/Logo_cnam.gif"/></a>
<p><br/></p>
<p><br/></p>
<p><br/></p>

In [1]:
from IPython.core.display import HTML
style=open('notebooks.css', "r").read()
HTML(style)

<center>
<i>-- Mécanique Spatiale --</i>
</center>

<div style="text-align:right">
<h1> TN n°4 </h1>
<img style="width:400px;float:left;" src="https://hpp.education/Lessons/MecaSpace/bannerentree.jpg" />
<h2> La rentrée Atmosphérique </h2>
<h3> - Utilisation et documentation  - </h3>
<h4> Trajectoires et paramètres importants  </h4>
<h6><a href="mailto:simon.marie@lecnam.net">simon.marie@lecnam.net</a></h6>
</div>

In [ ]:
import numpy as np
import scipy

import matplotlib
import matplotlib.pyplot as plt

#Option pour afficher les figures dans le notebook et eviter le plt.show():
%matplotlib inline  
plt.rc('xtick',labelsize=14)
plt.rc('ytick',labelsize=14)

In [ ]:
# Constante célestes:
G=6.67408e-11 # Constante de gravitation - 
Rt=6380000 # Rayon terrestre - m
Ms=1.9884e30 # Masse du soleil - kg
Mt=5.9722e24 # Masse de la terre - kg

<h1>Présentation</h1>

L'objectif de cette séance est d'étudier la trajectoire de rentrée atmosphérique d'un corps issue d'une orbite initiale connue.

La rentrée atmosphérique peut être annalysée suivant trois phases distinctes:
1. La manoeuvre de désorbitation visant à quitter l'orbite initiale.
2. La partie de la trajectoire visant à rejoindre les premières couches de l'atmosphère ($z\sim120$km). (Arc orbitale)
3. La partie purement atmosphérique souvent dimensionnante pour la mission (Arc atmosphérique). Nous distinguerons l'entrée sans portance dite balistique de l'entrée avec portance dite pilotée.

Lors de cette séance, nous ferons de nombreuses hypothèses simplificatrices pour faciliter les calculs:
* Orbites coplanaires (2D)
* Vitesse de rotation des corps céléstes non prise en compte.
* Coefficients de trainée et de portance indépendant du Mach (Valide en hypersonique mais faux en supersonique).


Ces hypothèses sont celles faites dans la théorie de la rentrée atmosphérique des travaux de <a href="https://hpp.education/Lessons/MecaSpace/Files/AllenEggers.pdf">Allen et Eggers</a> et permettent néanmoins de conserver les phénomènes importants intervenant dans les trajectoires de rentrée.

Enfin, il ne sera pas question dans cette séance d'étudier en détail les écoulements hypersoniques mis en jeux lors d'une rentrée atmosphérique et faisant intervenir des effets importants de dissociation moléculaire et de ionisation dues aux très fortes températures atteintes. Nous considérerons ici le flux thermique de façon simplifié comme présenté dans la théorie de <a href="https://hpp.education/Lessons/MecaSpace/Files/AllenEggers.pdf">Allen et Eggers</a>:

$$
\varphi=C_q\sqrt{\rho}u^3
$$


Ou $\varphi$ est en $W.m^{-2}$ et $C_q$ est un paramètre dépendant du type d'atmosphère et du véhicule de rentrée. Pour la terre, on prendra $C_q=1.705~ 10^{-4}$ USI.

On se focalisera dans cette séance sur le calcul des trajectoires possibles en fonction des paramètres de construction des capsules de rentrée (ou atterisseurs). Les trois principales grandeurs que l'on regardera pour dimensionner une mission de rentrée seront:

* La décélération subit par la capsule (particulièrment pour les rentrées habitées [<10g])
* Le flux thermique maximal pour le dimensionnement de la protection thermique (masse supplémentaire à prévoir)
* La pression dynamique maximal pour le dimensionnement des efforts subit par le lanceur pendant la rentrée.

<h5>Notes sur l'utilisation du module SOLSTICE </h5>

Afin de pouvoir experimenter les différents scénari de rentrée et de mieux comprendre l'importance de certains paramètres, vous disposez d'un "simulateur" de rentrée en important la classe <i>Capsule</i> du module <i>SOLSTICE</i>. Dans ce module, les équations du mouvement sont intégrées dans un repère polaire géocentrique.
Lors de votre première utilisation il vous faut télécharger la librairie SOLSTICE:

In [ ]:
#! wget https://hpp.education/Lessons/MecaSpace/Solstice/SOLSTICE.pyc

On peut ensuite l'importer:

In [ ]:
# Importation de la classe capsule
from SOLSTICE import Capsule

Comme toutes les classes en Python, on peut consulter la documentation. En python, la fonction help(Calss) renvoi la documentation de la class ainsi que la documentation de chaque méthode de classe:

In [ ]:
help(Capsule)

<h1> I - Désorbitation </h1>

La première phase de la rentrée consiste à sortir de l'orbite de "stationnement" pour bifurquer sur une orbite elliptique sécante à la surface d'"atterissage".

Pour cela, on procède à une manoeuvre orbitale en injectant de la quantité de mouvement $\Delta U$ suivant un angle choisit $\omega$.

<img style="width:60%;" src="https://hpp.education/Lessons/MecaSpace/Manoeuvre_schema.jpg" width=500/>


Avec les notations suivantes:

$$
\delta=\dfrac{\Delta U}{U_s}  ~~~ \xi=\dfrac{r_0}{r_e}  ~~~ k_0=\dfrac{U_0}{U_s}  ~~~ k_e=\dfrac{U_e}{U_s}
$$

On montre, en utilisant les relations (Al-Kashi) dans le triangle $(U_0,U_s,\Delta U)$ que:

$$
    U_0^2=U_s^2+\Delta U^2-2U_s\Delta U \cos(\pi-\omega)
$$

soit

$$
k_0=\sqrt{1+\delta^2+2\delta\cos(\omega)}\\
\sin(\gamma_0)=\dfrac{\delta \sin(\omega)}{k_0}
$$

<img style="float:left;" src="https://hpp.education/Lessons/MecaSpace/Rentree_schema.jpg"/>

En pratique, on considère une orbite initiale circulaire avec $U_s=\sqrt{\dfrac{GM_t}{r_s}}=\sqrt{\dfrac{GM_t}{r_0}}$.

Ainsi, la conservation de l'énergie sur l'arc orbital donne:

$$
\dfrac{1}{2}U_e^2-\dfrac{GM}{r_e}=\dfrac{1}{2}U_0^2-\dfrac{GM}{r_0}
$$

soit:

$$
U_e=U_s\sqrt{2\xi-1+\delta^2+2\delta\cos(\omega)}
$$

De la même façon, en utilisant la conservation du moment cinétique $r\dot{\theta}$ sur l'arc orbital soit:

$$
r_e U_e\cos(\gamma_e)=r_0 U_0\cos(\gamma_0)
$$

on peut exprimer l'angle de rentrée $\gamma_e$ en fonction des paramètres de manoeuvre $\delta$ et $\omega$ et du paramètre initial $\xi$:

$$
\cos(\gamma_e)=\xi\dfrac{1+\delta\cos(\omega)}{\sqrt{2\xi-1+\delta^2+2\delta\cos(\omega)}}
$$

<b> A partir des résultats précédents, créer une fonction permattant de trouver $U_e$ et $\gamma_e$ en fonction de $\Delta U$, $\omega$ et $r_0$ </b>

In [ ]:
def rentree(r0,du,w):
    us=...
    delta=...
    xi=...
    ...
    ue=...
    ge=...
    return ue,ge*180/np.pi


<b>Quel est l'angle et la vitesse de rentrée d'une capsule de rentrée quittant une orbite circulaire de 400km d'altitude avec une manoeuvre du type $(\Delta U, \omega)=(200,180°)$ ?</b>

In [ ]:
rentree(...,...,...) 

Ainsi, il est possible de déterminer les paramètres d'entrée $(U_e,\gamma_e)$ à partir d'une condition initiale ($U_s$,$r_0$) et des paramètres de manoeuvre ($\Delta U$,$\omega$). 

<b>A l'aide du module SOLSTICE fourni, placer une capsule sur une orbite circulaire à 400km d'altitude</b>

In [ ]:
zs=...
us=...
orb=Capsule(z0=zs,u=us)
print(orb)

<b>Calculer la position de la capsule au bout d'1 heure</b>

In [ ]:
orb.run(dt=1,ntmax=...)

<b>Effectuer une manoeuvre de $\Delta u=200$m/s avec $\omega=180°$ puis calculer la nouvelle position de la capsule, 20 minutes après la manoeuvre:</b>

In [ ]:
orb.mvr(200,180)
orb.run(dt=1,ntmax=20*60)

In [ ]:
orb.plotraj('polar')
plt.ylim(0,8000)

<b>Comparer les résultats à ceux calculés par la fonction rentree()</b>



Nous allons à présent étudier l'importance des paramètres d'entrée $(U_e,\gamma_e)$ sur la trajectoire et le dimensionnement mécanique de notre capsule de rentrée.

<h1> II - Une question de freinage </h1>

Considérons tout d'abord le cas le plus simple, en partant d'un corps en chute libre laché d'une altitude de 120km avec une vitesse initiale $U_s$ sous un angle de $90°$ avec l'horizontal local. Ce corp est soumis à son poid $P$ et à une force de trainée $F_d$.

<img style="width:60%;" src="https://hpp.education/Lessons/MecaSpace/Chute_schema.jpg"/>



Le bilan s'écrit:

$$
m\dfrac{dv}{dt}=P-F_d=mg_0-\dfrac{1}{2}\rho(z)v(z)^2*S C_d
$$

en définissant le coefficient balistique $\beta=\dfrac{S.C_d}{m}$, le bilan devient:

$$
\dfrac{dv}{dt}=\dfrac{mg_0-F_d}{m}=g_0-\dfrac{1}{2}\beta \rho(z)v(z)^2
$$

Ainsi la décélération subi par le corps est directement lié à la force de trainée:

$$
\Gamma=g_0-\dfrac{1}{2}\rho(z)v(z)^2\beta
$$

De la même façon que pour l'étape du décollage, on se donnera un modèle d'atmosphère du type:

$$
\rho(z)=\rho_0 e^{-z/z_0}
$$

Pour la terre on prendra les valeurs proposées par la théorie de <a href="https://hpp.education/Lessons/MecaSpace/Files/AllenEggers.pdf">Allen et Eggers</a> $Z_0=6700$m et $\rho_0=1.735$ $kg.m^{-3}$.

**Remarque:** Il est important de remarquer que les modèles d'atmosphère pour la rentrée et pour le départ, ne sont pas nécessairement les mêmes. En effet, pour la rentrée atmosphérique, on a généralement besoin de décrire l'atmosphère "par le haut" avec des vitesses d'approches très importantes.


En utilisant les hypothèses précédentes on peut facilement simplifier les équations du mouvement et montrer que la décélération maximale vaut:

$$
\Gamma_{max}=\dfrac{U_0^2 \sin(\gamma_0)}{2eZ_0}
$$

Elle ne dépend donc pas de la forme de la capsule !!
En revanche cette décélération maximale est atteinte pour:

$$
Z_g=Z_0\ln\left(\dfrac{\rho_0 Z_0  \beta }{\sin(\gamma_0)}\right)
$$

Qui dépend donc de la forme de la capsule à travers $\beta$.

**Remarque: Le coefficient balistique est parfois noté <a href="https://ntrs.nasa.gov/api/citations/20130010987/downloads/20130010987.pdf?attachment=true">$\zeta=\dfrac{1}{\beta}=\dfrac{m}{S C_d}$</a> et s'exprime en $kg/m^2$. Ici nous utiliserons $\beta$.**

Nous allons essayer de retrouver ce résultat par des simulations.



Le tableau suivant donne quelques exemples de coefficients $\beta$ pour des attérisseurs célèbres:

<table style="width:95%;font-size:20px;">
    <tr><th colspan=2>Capsule</th><th>Date</th><th>$C_d$</th><th>$S_{ref}$ (m2)</th><th>$m$ (kg)</th><th>$\beta$</th></tr>
    <tr><td><img src="https://upload.wikimedia.org/wikipedia/commons/8/8a/GeminiPatch.png" style="width:30px;vertical-align:middle;"/></td><td>Gemini</td><td>1964-1966</td><td>1.5265</td><td>4.1547</td><td>1982</td><td>$3.2$ $10^{-3}$</td></tr>
    <tr><td><img src="https://upload.wikimedia.org/wikipedia/commons/0/00/Apollo_program.svg?uselang=fr" style="width:30px;vertical-align:middle;"/></td><td><a href="https://ntrs.nasa.gov/archive/nasa/casi.ntrs.nasa.gov/19670027745.pdf">Apollo</a></td><td>1967-1974</td><td>1.2847</td><td>11.9459</td><td>5806</td><td>$2.6$ $10^{-3}$</td></tr>
    <tr><td><img src="https://www.esa.int/var/esa/storage/images/esa_multimedia/images/2009/11/soyuz_tma-4_flight_patch_2004/9915573-2-eng-GB/Soyuz_TMA-4_flight_patch_2004_pillars.jpg" style="width:30px;vertical-align:middle;"/></td><td><a href="https://fr.wikipedia.org/wiki/Soyouz_(v%C3%A9hicule_spatial)">Soyouz</a></td><td>1967-today</td><td>1.3254</td><td>3.6983</td><td>2850</td><td>$1.7$ $10^{-3}$</td></tr>
    <tr><td><img src="https://www.esa.int/var/esa/storage/images/esa_multimedia/images/2013/02/cassini-huygens_mission_logo/12518106-1-eng-GB/Cassini-Huygens_mission_logo_node_full_image_2.jpg" style="width:30px;vertical-align:middle;"/></td><td><a href="https://fr.wikipedia.org/wiki/Huygens_(sonde_spatiale)">Huygens</a></td><td>2004</td><td>1.1462</td><td>5.7255</td><td>318</td><td>$2.1$  $10^{-2}$</td></tr>
    <tr><td><img src="https://www.jpl.nasa.gov/missions/web/badge/insight.png" style="width:30px;vertical-align:middle;"/></td><td><a href="https://www.jpl.nasa.gov/news/press_kits/insight/landing/download/mars_insight_landing_presskit.pdf">Mars Insight</a></td><td>2018</td><td>1.2358</td><td>5.4739</td><td>358</td><td>$1.8$  $10^{-2}$</td></tr>
     <tr><td><img src="https://upload.wikimedia.org/wikipedia/commons/thumb/a/a9/Crew_Dragon_Demo-2_Patch.png/503px-Crew_Dragon_Demo-2_Patch.png" style="width:30px;vertical-align:middle;"/></td><td><a href="https://fr.wikipedia.org/wiki/Dragon_2#S%C3%A9lection_du_vaisseau_Crew_Dragon">Crew Dragon</a></td><td>2020</td><td>1.6418</td><td>10.7521</td><td>7500</td><td>$2.35$  $10^{-3}$</td></tr>
      <tr><td><img src="https://upload.wikimedia.org/wikipedia/commons/3/3c/Starliner_cft.png" style="width:30px;vertical-align:middle;"/></td><td><a href="https://fr.wikipedia.org/wiki/Boeing_CST-100_Starliner">CST-100</a></td><td>2022</td><td>1.5137</td><td>19.7923</td><td>8500</td><td>$3.5$  $10^{-3}$</td></tr>
    
    
    
</table>


<b>A l'aide du module SOLSTICE placer une capsule sur une orbite initiale de 120km d'altitude avec un angle de 90° (à la vertical)</b>

In [ ]:
gem=Capsule(gi=...,z0=...)
print(gem)

Par défaut la création de l'instance <i>gem</i> affiche les coordonées de la capsule: $z_0,\theta_0$, son orientation $\gamma$ et sa vitesse initiale $u$.

On peut alors calculer la trajectoire de la capsule en partant de ces conditions initiales. C'est la méthode run() qui permet de faire cela. Cette méthode réalise l'intégration des équations du mouvement. 

Lançons la capsule dans l'atmosphère:

In [ ]:
gem.run()

En pratique l'intégration s'arrête lorsque la capsule a atteint le sol (z=0) ou que le nombre d'itérations a atteint une limite fixée (par défaut $10^6$).

<b>Quelle est la vitesse de la capsule lors de l'impact au sol ? Quelle est la durée de la rentrée ?</b>

On peut représenter la trajectoire avec la méthode plotraj():

In [ ]:
gem.plotraj()

Rien de sensationnel en 1D....

Pour charger les données enregistrées pendant la simulation on utilise la méthode load():

In [ ]:
data=gem.load() # On charge les données enregistrtées pendant le "vol"

La méthode nous renvoi la structure du tableau de données "data". Ainsi data[:,0] contient le temps, data[:,1] l'altitude...

<b>Tracer l'évolution de la décélération en fonction de l'altitude et comparer la valeur max à celle estimer plus haut.</b>

In [ ]:
fig=plt.figure(figsize=(10,6),dpi=120)
# On calcul la deceleration maximal et son altitude
Z0,u0=6700,7910
rho0=1.735
Gm=... # Gamma max
Zg=... # Zg
plt.plot(Gm/9.81,Zg/1000,'sr')

# Comparons avec notre simulation:
plt.plot(data[:,7]/9.81,(data[:,1]-Rt)/1000);
plt.ylabel('Alt (km)');plt.xlabel('Deceleration (g)');

<b>Qu'observez-vous ?</b>

Regardons alors l'importance de l'angle $\gamma_e$ dans une trajectoire plus réaliste en 2D.

<h1> III - Rentrée balistique (sans portance) </h1>

Ici nous considérons que la rentrée se fait sous un angle initial $\gamma_e$. La capsule est soumise aux deux mêmes forces que précédemment mais avec une angle $\gamma$ quelconque:

<img style="width:70%;" src="https://hpp.education/Lessons/MecaSpace/Rentreebal_schema.jpg"/>

Les équations du mouvement dans le plan polaire $(r,\theta)$ s'écrivent:

$$
m(\ddot{r}-r\dot{\theta}^2) = -P+F_d\sin(\gamma_e)\\
m(r\ddot{\theta}+2\dot{r}\dot{\theta}) = -F_d\cos(\gamma_e)
$$


soit en divisant par la masse et en utilisant les notations introduites précédemment:

$$
\ddot{r}-r\dot{\theta}^2 = -\dfrac{\mathcal{G}M_t}{(R_t+r)^2}+\dfrac{1}{2}\rho(r)U^2\beta\sin(\gamma_e)\\
r\ddot{\theta}+2\dot{r}\dot{\theta} = -\dfrac{1}{2}\rho(r)U^2\beta\cos(\gamma_e)
$$

Ces équations sont intégrées dans la classe <i>Capsule</i>.

<b>A l'aide du module SOLSTICE, placer une capsule sur la même orbite que précédemment en changeant uniquement l'angle de rentré à $\gamma_e=6$, puis réaliser le calcul de la trajectoire:</b>

In [ ]:
gem=Capsule(gi=...,z0=...)
print(gem)

In [ ]:
gem.run()

<b>Quels est la vitesse de la capsule lors de l'impact au sol ? Quelle est la durée de la rentrée ?</b>
<b>Tracer la trajectoire à l'aide de la méthode plotraj()</b>

In [ ]:
fig=plt.figure(figsize=(15,5),dpi=120)
gem.plotraj()

<b>Que remarquez-vous ?</b>


<b>A l'aide de la méthode monit(fig) commenter l'évolution de la décélération et du flux thermique absorbé par la capsule</b>

In [ ]:
fig=plt.figure(figsize=(12,14),dpi=90)
gem.monit(fig)

<b>Conclusion ?</b>

<h1> IV - Rentrée pilotée (avec portance) </h1>

Les équations du mouvement a intégrer sont sensiblement les mêmes que dans le cas précédent, en ajoutant la force de portance. Le coefficient de portance est supposé constant et proportionel au coefficient de trainée:

$$
finesse=\dfrac{C_L}{C_D}
$$

<img style="width:60%;" src="https://hpp.education/Lessons/MecaSpace/Rentreeport_schema.jpg"/>

La finesse d'un vehicule de rentrée est plutôt faible ($\sim0.3$) et pouvait atteindre l'unité pour les (feu-)navettes américaines.

<b>En suivant la même procédure que précédemment, étudier la rentrée de la même capsule ayant une finesse de 0.3</b>

In [ ]:
cap=Capsule(gi=...,z0=...,fin=...,name='Rentree_port.dat')
print(cap)

In [ ]:
cap.run(dt=0.1)

In [ ]:
fig=plt.figure(figsize=(15,5),dpi=90)
cap.plotraj()

In [ ]:
fig=plt.figure(figsize=(12,14),dpi=90)
cap.monit(fig)
gem.monit(fig)

<b>Comparer alors les deux trajectoires. Que pouvez-vous dire ?</b>

<b>Maintenant, réaliser la même simulation en choisissant un angle de rentrée très faible de l'ordre du demi-degrès</b>

In [ ]:
cap2=Capsule(gi=...,z0=...,fin=...,name='Rentree_port2.dat')
cap2.run(dt=0.1)

In [ ]:
fig=plt.figure(figsize=(12,4),dpi=90)
cap2.plotraj()

In [ ]:
fig=plt.figure(figsize=(12,18),dpi=90)
cap2.monit(fig)

<b>Qu'observez-vous ?</b>

<h1> V - Mission Complète </h1>

Maintenant vous devez pouvoir revenir sur terre en un point précis à partir d'une orbite donnée:

<b>En partant d'une capsule de type "Orion" de finesse $0.26$, initialement sur une orbite circulaire de 350 km d'altitude, vous devez atterir au point $\theta = 272°$ avec les contraintes suivantes: $\Gamma<10g$ et $\varphi<1000 kW/m^2$, précision$<100m$</b>

In [ ]:
cap3=Capsule(gi=0,z0=...,u=...,beta=...,fin=...)
cap3.run(dt=0.1,ntmax=60*60*5.65)
cap3.mvr(???,???)
cap3.run(dt=0.1)
cap3.plotraj()
print("precision= "+str(Rt*(((180*cap3.theta/np.pi)-272)*np.pi/180))+" m")

In [ ]:
fig=plt.figure(figsize=(16,16))
cap3.monit(fig)

<b>Y'a t'il unicité de la solution ?</b>
<b>Si non comment pourrait-on calculer la manoeuvre optimale nécéssitant le moins de carburant ?</b>

<h1> VI - Quelques notions sur les dispositifs de freinages </h1>

Comme nous l'avons vu, le flux thermique auquel est soumis le véhicule de rentrée peut rester important même avec des angles de rentrée relativement faibles ($500-800$ $kW/m^2$). Ainsi la <a href="https://fr.wikipedia.org/wiki/Bouclier_thermique">protection thermique</a> devient indispensable pour assurer l'intégrité du véhicule. 

Deux solutions sont possibles:
* les protections rayonnantes pour les rentrées plannées à faibles $\gamma_e$ 
* les protections ablatives pour les rentrées balistiques à $\gamma_e$ plus élevé engeandrant des flux thermique plus importants.


<h2> 1 - Protections thermiques Rayonnantes</h2>

Pour ce type de protection, la paroi externe du bouclier emet un flux thermique par rayonement qui est en équilibre thermique avec le flux convectif incident. D'après la loi de <i>Stephan-Boltzmann</i>, on a donc en notant $T_p$ la température de paroi:

$$
\varphi_{i}=\varphi_{rayonement}=\epsilon\sigma T_p^4
$$

soit:

$$
T_p=\left(\dfrac{\varphi_i}{\epsilon\sigma}\right)^{(1/4)}
$$

$\sigma=5.670367~ 10^{-8}$ $W.m^{-2}.K^{-4}$
$\epsilon$: émissivité du materiaux

Voici quelques candidats pour la construction de ce type de protection

<table style="font-size:20px;width:70%;">
    <tr><th>Materiaux</th><th>$T_{max}$ °C</th><th>$\epsilon$</th><th>$\sim \varphi_{max}$ ($kW/m^2$)</th></tr>
    <tr><td>Carbure de silicium</td><td>1900</td><td>0.89</td><td>1100</td></tr>
<tr><td>niobium</td><td>1300</td><td>0.89</td><td>310</td></tr>
<tr><td>Fibre de zircone</td><td>1400</td><td>0.84</td><td>380</td></tr>
<tr><td>Tantale</td><td>1500</td><td>0.64</td><td>360</td></tr>
</table>



<b>En se basant sur vos résultat, estimer les températures de paroi des différentes rentrées que vous avez effectuées</b>

In [ ]:
traj_data=cap.load()
phi=traj_data[:,6]
Tp=...

<h2> 2 - Protections thermiques Ablatives</h2>

Ce deuxième type de protection est basée sur le principe de l'absorbtion de la chaleur par des réactions endothermiques de type changement d'état (fusion, sublimation, vaporisation...).

Dans ce cas, la surface subissant le flux thermique reste à température constante $T_a$ appellée température d'ablation. On peut écrire un modèle très simplifié d'évolution du front d'ablation $s$:

$$
\varphi(t)\sim\rho_a H_a \dfrac{\partial s}{\partial t}
$$



<table style="font-size:20px;width:900px;">
<tr><th>Materiaux</th><th>$T_{a}$ (°C)</th><th>$\rho$ (kg/$m^3$)</th><th>$H_a$ (kJ/kg)</th></tr>
<tr><td>Carbon Phenolic FM5055</td><td>2000</td><td>1450</td><td>60000</td></tr>
<tr><td>Super Lightweight Ablator SLA561V</td><td>1500</td><td>260</td><td>49000</td></tr>
    <tr><td>ULD100 MDac</td><td>1073</td><td>250</td><td>45000</td></tr>

<tr><td></td><td></td><td></td><td></td></tr>
</table>

On peut donc estimer globalement:

$$
\mathcal{e}\sim\int_{t_0}^{t_1}\dfrac{\varphi(t)}{\rho_a H_a}dt
$$

<b>A partir des résultats de la dernière simulation, estimer la taille et la masse du bouclier thermique a utiliser pour absorber le flux thermique incident</b>

In [ ]:
e=...
print('ep= ',e)

<b>Conculsion</b>

<h2> 3 - Parachute supersonique</h2>

Lorsque le nombre de Mach local a atteint des niveaux supersoniques raisonable ($\sim 1.5$), on peut utiliser un système de freinage basé sur le déploiement d'un parachute supersonique.
En pratique la décélération de basse atmosphère dépend énormément de la mission et du type d'atmosphère. Sur ce sujet, on pourra consulter les références données en conclusion.

In [ ]:
from IPython.display import YouTubeVideo
YouTubeVideo('AcAgnQ9K7UY',width=900,height=400)

# Conclusion

Rédigez une synthèse de toutes les notions que vous avez parcourues dans ce projet.


# Références

Voici quelques références qui ont servi a mettre au point ce notebook. Les lecteurs intéressés pourront approfondir de nombreux sujets en les parcourant.

* <a href="https://hpp.education/Lessons/MecaSpace/Files/AllenEggers.pdf"> Allen & Eggers - 1953 </a>
* <a href="http://www.sudoc.abes.fr/DB=2.1/SRCH?IKT=12&TRM=003322351">Systèmes Spatiaux - D.Marty - 1994</a>
* <a href="https://www.nasa.gov/pdf/695726main_ComingHome-ebook.pdf"> Coming Home (NASA)</a>
* <a href="https://www.youtube.com/watch?v=-l7MM9yoxII">Undocking from ISS (ESA)</a>
* <a href="https://en.wikipedia.org/wiki/Atmospheric_entry"> Atmospheric rentry (WIKI) </a>
* <a href="https://fr.wikipedia.org/wiki/Low-Density_Supersonic_Decelerator"> LDSD (WIKI) </a>



<img id="top" style="float:right;height:100px;" src="http://ich.cnam.fr/medias/photo/omnes-ubique-docet_1472542836182-gif?ID_FICHE=580363">
<a style="float:left;" href="http://www.cnam.fr//"><img style="height:100px;" src="https://upload.wikimedia.org/wikipedia/commons/6/66/Logo_cnam.gif"/></a>
<center><a href="#top">Retour en haut de la page</a></center>